<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Data-Preprocessing" data-toc-modified-id="Data-Preprocessing-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Data Preprocessing</a></span><ul class="toc-item"><li><span><a href="#Geographic-Data-Preprocessing" data-toc-modified-id="Geographic-Data-Preprocessing-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Geographic Data Preprocessing</a></span></li><li><span><a href="#Coronavirus-Data-Preprocessing" data-toc-modified-id="Coronavirus-Data-Preprocessing-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Coronavirus Data Preprocessing</a></span></li></ul></li><li><span><a href="#Visualization" data-toc-modified-id="Visualization-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Visualization</a></span><ul class="toc-item"><li><span><a href="#Spread-of-Coronavirus-in-China" data-toc-modified-id="Spread-of-Coronavirus-in-China-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Spread of Coronavirus in China</a></span></li><li><span><a href="#Geographic-Visualization" data-toc-modified-id="Geographic-Visualization-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Geographic Visualization</a></span></li><li><span><a href="#Death-Rate-and-Cure-Rate" data-toc-modified-id="Death-Rate-and-Cure-Rate-2.3"><span class="toc-item-num">2.3&nbsp;&nbsp;</span>Death Rate and Cure Rate</a></span></li><li><span><a href="#Growth-Rate" data-toc-modified-id="Growth-Rate-2.4"><span class="toc-item-num">2.4&nbsp;&nbsp;</span>Growth Rate</a></span></li></ul></li></ul></div>

# Data Preprocessing

In [1]:
import json
import folium
import webbrowser
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import folium.plugins as plugins
from folium.plugins import HeatMap

## Geographic Data Preprocessing

In [434]:
# load the json file of latitude and longtitude data
with open('/Users/hkmac/Desktop/region.json') as f: 
    region = json.load(f)

In [436]:
longitude = []
latitude = []
region_name = []

In [437]:
# get province,longitude,and latitude to create a daraframe of province's geographic data
# this part is for geographic visualization
longitude = []
latitude = []
region_name = []

for i in region['districts']:
    if i['level'] == 'province': 
        region_name.append(i['name'])
        longitude.append(i["center"]["longitude"])
        latitude.append(i["center"]["latitude"])

region_lookup = pd.DataFrame({'province':region_name,"longitude":longitude,"latitude":latitude})
region_lookup.head()

province   longitude   latitude
0  澳门特别行政区  113.543028  22.186835
1      北京市  116.407394  39.904211
2      重庆市  106.551643  29.562849
3      福建省  119.295143  26.100779
4      广东省  113.266410  23.132324

## Coronavirus Data Preprocessing

In [438]:
covidData = pd.read_csv("/Users/hkmac/Desktop/ncovdata.csv")

In [439]:
covidData.head()

provinceName cityName  province_confirmedCount  province_suspectedCount  \
0          上海市   外地来沪人员                      318                        0   
1          上海市     浦东新区                      318                        0   
2          上海市      宝山区                      318                        0   
3          上海市      徐汇区                      318                        0   
4          上海市      闵行区                      318                        0   

   province_curedCount  province_deadCount  city_confirmedCount  \
0                   90                   1                  102   
1                   90                   1                   56   
2                   90                   1                   20   
3                   90                   1                   17   
4                   90                   1                   18   

   city_suspectedCount  city_curedCount  city_deadCount  \
0                    0               27               1   
1                    0               12               0   
2                    0                1               0   
3                    0                2               0   
4                    0                4               0   

                updateTime  
0  2020-02-15 00:41:46.976  
1  2020-02-15 00:41:46.976  
2  2020-02-15 00:41:46.976  
3  2020-02-15 00:41:46.976  
4  2020-02-15 00:41:46.976

In [440]:
# take a look at some information about this dataset
covidData.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 39302 entries, 0 to 39301
Data columns (total 11 columns):
provinceName               39302 non-null object
cityName                   39302 non-null object
province_confirmedCount    39302 non-null int64
province_suspectedCount    39302 non-null int64
province_curedCount        39302 non-null int64
province_deadCount         39302 non-null int64
city_confirmedCount        39302 non-null int64
city_suspectedCount        39302 non-null int64
city_curedCount            39302 non-null int64
city_deadCount             39302 non-null int64
updateTime                 39302 non-null object
dtypes: int64(8), object(3)
memory usage: 3.3+ MB


In [441]:
covidData.dtypes

provinceName               object
cityName                   object
province_confirmedCount     int64
province_suspectedCount     int64
province_curedCount         int64
province_deadCount          int64
city_confirmedCount         int64
city_suspectedCount         int64
city_curedCount             int64
city_deadCount              int64
updateTime                 object
dtype: object

In [442]:
# convert the datatype of updateTime to datetime64, and get date from that column as a new column
def datimeTrans(dataset):
    dataset["updateTime"] = dataset["updateTime"].apply(pd.to_datetime)
    dataset["date"] = dataset["updateTime"].dt.date.apply(pd.to_datetime)
    return dataset

In [443]:
covidData = datimeTrans(covidData)

In [444]:
# here I just momentarily convert the datatype to string
covidData["date"] = covidData["date"].astype(str)

In [445]:
date = []

I find out that there are many duplicated data in a single day. In order to group our data by different province every single day, I am going to delete everyday's repetitive records.

In [446]:
def deldup(dataset):    
    for i in range(len(dataset)):
        province = dataset.loc[i,"provinceName"]
        city = dataset.loc[i,"cityName"]
        if dataset.loc[i,"date"] not in date:
            date.append(dataset.loc[i,"date"])
            provinces = []
            citys = []
        if province not in provinces:
            provinces.append(province)
        if (province in provinces) & (city in citys):
            dataset = dataset.drop(i)
        if (province in provinces) & (city not in citys):
            citys.append(city)
    return dataset

In [447]:
covidData = deldup(covidData)

In [448]:
covidData.describe()

province_confirmedCount  province_suspectedCount  province_curedCount  \
count              8171.000000              8171.000000          8171.000000   
mean               1033.247093                49.546812            76.724024   
std                4701.879561              1077.149318           317.273409   
min                   1.000000                 0.000000             0.000000   
25%                  75.000000                 0.000000             1.000000   
50%                 184.000000                 0.000000            11.000000   
75%                 428.000000                 0.000000            44.000000   
max               51986.000000             23638.000000          3900.000000   

       province_deadCount  city_confirmedCount  city_suspectedCount  \
count         8171.000000          8171.000000          8171.000000   
mean            23.234977            62.054461             0.000857   
std            133.796531           732.893854             0.036683   
min              0.000000             0.000000             0.000000   
25%              0.000000             3.000000             0.000000   
50%              0.000000             8.000000             0.000000   
75%              1.000000            20.000000             0.000000   
max           1318.000000         35991.000000             2.000000   

       city_curedCount  city_deadCount  
count      8171.000000     8171.000000  
mean          4.612410        1.365072  
std          44.293164       25.622139  
min           0.000000        0.000000  
25%           0.000000        0.000000  
50%           0.000000        0.000000  
75%           2.000000        0.000000  
max        2023.000000     1036.000000

In [449]:
dayUnique = pd.DataFrame()
dayUnique = covidData.groupby(['provinceName', 'date'])['city_confirmedCount'].aggregate('sum').unstack()
dayUnique

date          2020-01-24  2020-01-25  2020-01-26  2020-01-27  2020-01-28  \
provinceName                                                               
上海市                  NaN         NaN         NaN        53.0        96.0   
云南省                  5.0        11.0        16.0        26.0        44.0   
内蒙古自治区               1.0         7.0         7.0        22.0        30.0   
北京市                 51.0        41.0        68.0        80.0        91.0   
吉林省                  3.0         4.0         NaN         6.0         8.0   
四川省                 15.0        28.0        44.0        69.0        90.0   
天津市                  NaN         NaN        14.0        22.0        24.0   
宁夏回族自治区              2.0         3.0         4.0         7.0        11.0   
安徽省                 15.0        39.0        60.0        70.0       106.0   
山东省                 15.0        27.0        46.0        75.0        95.0   
山西省                  1.0         6.0         9.0        13.0        20.0   
广东省                 54.0        78.0       111.0       151.0       208.0   
广西壮族自治区             13.0        23.0        36.0        46.0        51.0   
新疆维吾尔自治区             NaN         3.0         4.0         5.0        10.0   
江苏省                  9.0        18.0        33.0        47.0        70.0   
江西省                  7.0        18.0        36.0        48.0        72.0   
河北省                  2.0         8.0        13.0        18.0        33.0   
河南省                  9.0        32.0        86.0       133.0       188.0   
浙江省                 43.0        62.0       104.0       128.0       173.0   
海南省                  8.0        19.0        22.0        33.0        40.0   
湖北省                549.0       761.0      1058.0      1423.0      2714.0   
湖南省                 24.0        43.0        69.0       100.0       143.0   
澳门                   NaN         NaN         2.0         NaN         NaN   
甘肃省                  2.0         5.0         7.0        14.0        22.0   
福建省                 10.0        18.0        35.0        59.0        80.0   
西藏自治区                NaN         NaN         NaN         NaN         NaN   
贵州省                  3.0         4.0         5.0         7.0         9.0   
辽宁省                  3.0        14.0        19.0        25.0        32.0   
重庆市                 27.0        57.0        75.0       110.0       132.0   
陕西省                  5.0        15.0        22.0        35.0        46.0   
青海省                  NaN         1.0         NaN         6.0         NaN   
黑龙江省                 4.0         9.0        15.0        21.0        30.0   

date          2020-01-29  2020-01-30  2020-01-31  2020-02-01  2020-02-02  \
provinceName                                                               
上海市                 96.0       112.0       233.0       169.0       182.0   
云南省                 55.0        70.0        83.0        93.0       105.0   
内蒙古自治区              16.0        18.0        19.0        23.0        27.0   
北京市                111.0        90.0       260.0       168.0       191.0   
吉林省                  9.0        14.0        14.0        18.0        23.0   
四川省                108.0       142.0       177.0       207.0       231.0   
天津市                 31.0        32.0        33.0        41.0        48.0   
宁夏回族自治区             12.0        18.0        21.0        26.0        28.0   
安徽省                155.0       200.0       237.0       297.0       340.0   
山东省                130.0       158.0       184.0       206.0       230.0   
山西省                 30.0        35.0        39.0        47.0        56.0   
广东省                282.0       354.0       436.0       535.0       632.0   
广西壮族自治区             58.0        78.0        87.0       100.0       111.0   
新疆维吾尔自治区            15.0        14.0        19.0        18.0        21.0   
江苏省                 99.0       129.0       168.0       202.0       236.0   
江西省                109.0       162.0       240.0       286.0       333.0   
河北省                 48.0        65.0        82.

There are many missing value in this dataframe. To deal with this case, NaN in the first column must be 0. For the other columns, I am going to fill these NaN regarding the previous column.

In [450]:
def nullhandling(dataset):
    dataset.iloc[:,0].fillna(0,inplace = True)
    for j in range(len(dataset)):
        for i in range(len(dataset.columns)):
            if i == 0:
                continue
            elif dataset.isnull().iloc[j,i] == False:
                continue
            else:
                dataset.iloc[j,i] = dataset.iloc[j,i-1]
    return dataset

In [451]:
dayUnique = nullhandling(dayUnique)
dayUnique

date          2020-01-24  2020-01-25  2020-01-26  2020-01-27  2020-01-28  \
provinceName                                                               
上海市                  0.0         0.0         0.0        53.0        96.0   
云南省                  5.0        11.0        16.0        26.0        44.0   
内蒙古自治区               1.0         7.0         7.0        22.0        30.0   
北京市                 51.0        41.0        68.0        80.0        91.0   
吉林省                  3.0         4.0         4.0         6.0         8.0   
四川省                 15.0        28.0        44.0        69.0        90.0   
天津市                  0.0         0.0        14.0        22.0        24.0   
宁夏回族自治区              2.0         3.0         4.0         7.0        11.0   
安徽省                 15.0        39.0        60.0        70.0       106.0   
山东省                 15.0        27.0        46.0        75.0        95.0   
山西省                  1.0         6.0         9.0        13.0        20.0   
广东省                 54.0        78.0       111.0       151.0       208.0   
广西壮族自治区             13.0        23.0        36.0        46.0        51.0   
新疆维吾尔自治区             0.0         3.0         4.0         5.0        10.0   
江苏省                  9.0        18.0        33.0        47.0        70.0   
江西省                  7.0        18.0        36.0        48.0        72.0   
河北省                  2.0         8.0        13.0        18.0        33.0   
河南省                  9.0        32.0        86.0       133.0       188.0   
浙江省                 43.0        62.0       104.0       128.0       173.0   
海南省                  8.0        19.0        22.0        33.0        40.0   
湖北省                549.0       761.0      1058.0      1423.0      2714.0   
湖南省                 24.0        43.0        69.0       100.0       143.0   
澳门                   0.0         0.0         2.0         2.0         2.0   
甘肃省                  2.0         5.0         7.0        14.0        22.0   
福建省                 10.0        18.0        35.0        59.0        80.0   
西藏自治区                0.0         0.0         0.0         0.0         0.0   
贵州省                  3.0         4.0         5.0         7.0         9.0   
辽宁省                  3.0        14.0        19.0        25.0        32.0   
重庆市                 27.0        57.0        75.0       110.0       132.0   
陕西省                  5.0        15.0        22.0        35.0        46.0   
青海省                  0.0         1.0         1.0         6.0         6.0   
黑龙江省                 4.0         9.0        15.0        21.0        30.0   

date          2020-01-29  2020-01-30  2020-01-31  2020-02-01  2020-02-02  \
provinceName                                                               
上海市                 96.0       112.0       233.0       169.0       182.0   
云南省                 55.0        70.0        83.0        93.0       105.0   
内蒙古自治区              16.0        18.0        19.0        23.0        27.0   
北京市                111.0        90.0       260.0       168.0       191.0   
吉林省                  9.0        14.0        14.0        18.0        23.0   
四川省                108.0       142.0       177.0       207.0       231.0   
天津市                 31.0        32.0        33.0        41.0        48.0   
宁夏回族自治区             12.0        18.0        21.0        26.0        28.0   
安徽省                155.0       200.0       237.0       297.0       340.0   
山东省                130.0       158.0       184.0       206.0       230.0   
山西省                 30.0        35.0        39.0        47.0        56.0   
广东省                282.0       354.0       436.0       535.0       632.0   
广西壮族自治区             58.0        78.0        87.0       100.0       111.0   
新疆维吾尔自治区            15.0        14.0        19.0        18.0        21.0   
江苏省                 99.0       129.0       168.0       202.0       236.0   
江西省                109.0       162.0       240.0       286.0       333.0   
河北省                 48.0        65.0        82.

In [452]:
dayUnique.style.background_gradient(cmap='gnuplot')

Because the data range Hubei province is much larger than others, I just provisionally remove Hubei's data to visualize spread of Coronavirus. Later I will focus on the spread of Coronavirus within Hubei province separately.

In [453]:
dayUnique_drophb = dayUnique.drop("湖北省")
dayUnique_drophb.style.background_gradient(cmap='twilight_shifted')

# Visualization
## Spread of Coronavirus in China 

In [454]:
dayUnique_drophb = dayUnique_drophb.T.reset_index()
dayUnique = dayUnique.T.reset_index()

In [455]:
listofcolumns = []
for i in dayUnique_drophb.columns:
    if i != "date":
        listofcolumns.append(i)

dayUnique_drophb_melt = pd.melt(dayUnique_drophb, id_vars=['date'],
                                value_vars= listofcolumns, 
                                var_name='Province', value_name='Count')

In [456]:
listofcolumns = []
for i in dayUnique.columns:
    if i != "date":
        listofcolumns.append(i)

dayUnique_melt = pd.melt(dayUnique, id_vars=['date'],
                                value_vars= listofcolumns, 
                                var_name='Province', value_name='Count')

In [457]:
px.line(dayUnique_melt, x="date", y="Count",color ='Province',
        title='Outbreak in China from Jan 25 - Feb 15')

In [458]:
px.line(dayUnique_drophb_melt, x="date", y="Count",color ='Province',
        title='Outbreak in China (excluding Hubei Province) from Jan 25 - Feb 15')

In [459]:
fig = px.bar(dayUnique_melt, 
             y="date", x="Count", color='Province', orientation='h', height=700,
             title='Number of Confirmed in China')
fig.update_layout(uniformtext_minsize=5, uniformtext_mode='hide')
fig.show()

In [460]:
fig = px.bar(dayUnique_drophb_melt, 
             y="date", x="Count", color='Province', orientation='h', height=700,
             title='Number of Confirmed in China (excluding Hubei Province)')
fig.update_layout(uniformtext_minsize=5, uniformtext_mode='hide')
fig.show()

In [461]:
px.bar(dayUnique_melt,x="Count", y="Province", color='Province', 
       orientation='h', height=800,title='Outbreak in China',
       animation_frame="date",range_x = [0,65000])

In [464]:
px.bar(dayUnique_drophb_melt,x="Count", y="Province", color='Province', 
       orientation='h', height=800,title='Outbreak in China (excluding Hubei Province)',
       animation_frame="date",range_x=[0,1400])

In [465]:
px.treemap(dayUnique_drophb_melt.sort_values(by='Count', ascending=False).reset_index(drop=True), 
           path=["Province"], values="Count")

In [467]:
dayUnique = pd.DataFrame()
dayUnique = covidData.groupby(['provinceName', 'date'])['city_confirmedCount'].aggregate('sum').unstack()
dayUnique.head()

date          2020-01-24  2020-01-25  2020-01-26  2020-01-27  2020-01-28  \
provinceName                                                               
上海市                  NaN         NaN         NaN        53.0        96.0   
云南省                  5.0        11.0        16.0        26.0        44.0   
内蒙古自治区               1.0         7.0         7.0        22.0        30.0   
北京市                 51.0        41.0        68.0        80.0        91.0   
吉林省                  3.0         4.0         NaN         6.0         8.0   

date          2020-01-29  2020-01-30  2020-01-31  2020-02-01  2020-02-02  \
provinceName                                                               
上海市                 96.0       112.0       233.0       169.0       182.0   
云南省                 55.0        70.0        83.0        93.0       105.0   
内蒙古自治区              16.0        18.0        19.0        23.0        27.0   
北京市                111.0        90.0       260.0       168.0       191.0   
吉林省                  9.0        14.0        14.0        18.0        23.0   

date          2020-02-03  2020-02-04  2020-02-05  2020-02-06  2020-02-07  \
provinceName                                                               
上海市                203.0       219.0       243.0       257.0       277.0   
云南省                114.0       119.0       124.0       133.0       136.0   
内蒙古自治区              34.0        35.0        42.0        46.0        50.0   
北京市                212.0       228.0       253.0       274.0       297.0   
吉林省                 31.0        47.0        54.0        59.0        65.0   

date          2020-02-08  2020-02-09  2020-02-10  2020-02-11  2020-02-12  \
provinceName                                                               
上海市                286.0       293.0       299.0       303.0       311.0   
云南省                138.0       141.0       149.0       153.0       154.0   
内蒙古自治区              52.0        54.0        58.0         NaN        60.0   
北京市                315.0       326.0       337.0       342.0       352.0   
吉林省                 69.0        78.0        80.0        81.0        83.0   

date          2020-02-13  2020-02-14  2020-02-15  
provinceName                                      
上海市                315.0       318.0       318.0  
云南省                156.0       162.0         NaN  
内蒙古自治区              61.0        65.0         NaN  
北京市                366.0       372.0         NaN  
吉林省                 84.0        86.0         NaN

In [468]:
dayUnique_wuhan = covidData[covidData["provinceName"] == "湖北省"]
dayUnique_wuhan = dayUnique_wuhan.groupby(['cityName', 'date'])['city_confirmedCount'].aggregate('sum').unstack()

In [469]:
# I have defined this function at the begining
dayUnique_wuhan = nullhandling(dayUnique_wuhan)
dayUnique_wuhan.style.background_gradient(cmap='rainbow')

In [470]:
dayUnique_wuhan = dayUnique_wuhan.T.reset_index()
listofcolumns = []
# get all of the column names, store in a list
for i in dayUnique_wuhan.columns:
    if i != "date":
        listofcolumns.append(i)

dayUnique_wuhan_melt = pd.melt(dayUnique_wuhan, id_vars=['date'],
                                value_vars= listofcolumns, 
                                var_name='Province', value_name='Count')

In [471]:
fig = px.bar(dayUnique_wuhan_melt, 
             y="date", x="Count", color='Province', orientation='h', height=700,
             title='Number of Confirmed in Hubei Province')
fig.update_layout(uniformtext_minsize=5, uniformtext_mode='hide')
fig.show()

In [472]:
px.bar(dayUnique_wuhan_melt,x="Count", y="Province", color='Province', 
       orientation='h', height=800,title='Outbreak in Hubei Province',
       animation_frame="date",range_x = [0,38000])

In [473]:
px.treemap(dayUnique_wuhan_melt.sort_values(by='Count', ascending=False).reset_index(drop=True), 
           path=["Province"], values="Count")

## Geographic Visualization

In [474]:
dayUnique_melt_region = pd.merge(region_lookup,dayUnique_melt,
                                left_on="province",right_on="Province",how='outer')

In [475]:
# here, some province name doesn't match
dayUnique_melt_region.isnull().sum()

province     23
longitude    23
latitude     23
date          3
Province      3
Count         3
dtype: int64

In [476]:
# let's find it
dayUnique_melt_region.head()

province   longitude   latitude        date Province  Count
0  澳门特别行政区  113.543028  22.186835         NaN      NaN    NaN
1      北京市  116.407394  39.904211  2020-01-24      北京市   51.0
2      北京市  116.407394  39.904211  2020-01-25      北京市   41.0
3      北京市  116.407394  39.904211  2020-01-26      北京市   68.0
4      北京市  116.407394  39.904211  2020-01-27      北京市   80.0

In [477]:
# let's find it
for i in list(set(dayUnique_melt["Province"])):
    if i in region_lookup["province"].values:
        pass
    else:
        print(i)

澳门


In [478]:
region_lookup['province'][0] = '澳门'

/Users/hkmac/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [479]:
del dayUnique_melt_region
dayUnique_melt_region = pd.merge(region_lookup,dayUnique_melt,
                                left_on="province",right_on="Province",how='outer')
del dayUnique_melt_region["province"]

In [480]:
dayUnique_melt_region.isnull().sum()

longitude    0
latitude     0
date         2
Province     2
Count        2
dtype: int64

In [481]:
dayUnique_melt_region = dayUnique_melt_region.dropna()
dayUnique_melt_region.dtypes

longitude    float64
latitude     float64
date          object
Province      object
Count        float64
dtype: object

In [482]:
# select only 2020-02-14
# currently data of 02-15 is incomplete
dayUnique_melt_region["date"] = dayUnique_melt_region["date"].apply(pd.to_datetime)
dayUnique_melt_region_lastday = dayUnique_melt_region.query("date == '2020-02-14'")
dayUnique_melt_region_lastday.head()

longitude   latitude       date Province   Count
21   113.543028  22.186835 2020-02-14       澳门     2.0
44   116.407394  39.904211 2020-02-14      北京市   372.0
67   106.551643  29.562849 2020-02-14      重庆市   532.0
90   119.295143  26.100779 2020-02-14      福建省   281.0
113  113.266410  23.132324 2020-02-14      广东省  1261.0

In [483]:
covmap = folium.Map(location=[36, 105], zoom_start=4)

for lat, lon, value, name in zip(dayUnique_melt_region_lastday["latitude"], 
                                 dayUnique_melt_region_lastday['longitude'], 
                                 dayUnique_melt_region_lastday['Count'], 
                                 dayUnique_melt_region_lastday['Province']):
    folium.CircleMarker([lat, lon],
                        radius=20,
                        popup = ('Province: ' + str(name) + '<br>'
                        'Confrimed: ' + str(value) + '<br>'),
                        color='red',
                        
                        fill_color='red',
                        fill_opacity=0.7 ).add_to(covmap)


covmap

In [484]:
# convert data into lists that can be used by folium
num = dayUnique_melt_region_lastday.shape[0]
lat = np.array(dayUnique_melt_region_lastday["latitude"][0:num])
lon = np.array(dayUnique_melt_region_lastday['longitude'][0:num])
confrimed = np.array(dayUnique_melt_region_lastday['Count'][0:num])
mapdata = [[lat[i], lon[i], confrimed[i]] for i in range(num)]

In [485]:
heatmap = folium.Map(location=[38, 100], zoom_start=4)
HeatMap(mapdata).add_to(heatmap)

In [486]:
# visualize the spread of COVID-19 
heatmap

## Death Rate and Cure Rate

In [487]:
dayunique_dq = covidData.query("date == '2020-02-14'").groupby(['provinceName', 'date'])["city_curedCount","city_deadCount","city_confirmedCount"].aggregate('sum').unstack()

In [488]:
# create two new columns of cure rate and death rate
dayunique_dq["cure rate"] = dayunique_dq["city_curedCount"]/dayunique_dq["city_confirmedCount"]
dayunique_dq["death rate"] = dayunique_dq["city_deadCount"]/dayunique_dq["city_confirmedCount"]

In [489]:
dayunique_dq.drop(["city_curedCount","city_deadCount","city_confirmedCount"],axis=1,inplace=True)
dayunique_dq.reset_index(inplace=True)
dayunique_dq.head()

provinceName cure rate death rate
date                                  
0             上海市  0.194969   0.003145
1             云南省  0.209877   0.000000
2          内蒙古自治区  0.092308   0.000000
3             北京市  0.024194   0.000000
4             吉林省  0.290698   0.011628

In [490]:
px.bar(dayunique_dq,x="provinceName",y="cure rate",
       color="provinceName",title='Cure rate of each province')

In [491]:
px.bar(dayunique_dq,x="provinceName",y="death rate",
       color="provinceName",title='Death rate of each province')

## Growth Rate

In [497]:
dayUnique_gr = dayUnique.T
dayUnique_gr.drop(["2020-01-24","2020-01-25","2020-01-26"],inplace=True)
dayUnique_gr.drop(["澳门","西藏自治区"],axis=1,inplace=True)

In [498]:
pd.set_option('display.max_columns', None)
dayUnique_gr.head(10)

provinceName    上海市    云南省  内蒙古自治区    北京市   吉林省    四川省   天津市  宁夏回族自治区    安徽省  \
date                                                                           
2020-01-27     53.0   26.0    22.0   80.0   6.0   69.0  22.0      7.0   70.0   
2020-01-28     96.0   44.0    30.0   91.0   8.0   90.0  24.0     11.0  106.0   
2020-01-29     96.0   55.0    16.0  111.0   9.0  108.0  31.0     12.0  155.0   
2020-01-30    112.0   70.0    18.0   90.0  14.0  142.0  32.0     18.0  200.0   
2020-01-31    233.0   83.0    19.0  260.0  14.0  177.0  33.0     21.0  237.0   
2020-02-01    169.0   93.0    23.0  168.0  18.0  207.0  41.0     26.0  297.0   
2020-02-02    182.0  105.0    27.0  191.0  23.0  231.0  48.0     28.0  340.0   
2020-02-03    203.0  114.0    34.0  212.0  31.0  254.0  60.0     31.0  408.0   
2020-02-04    219.0  119.0    35.0  228.0  47.0  282.0  67.0     34.0  480.0   
2020-02-05    243.0  124.0    42.0  253.0  54.0  301.0  69.0      NaN  530.0   

provinceName    山东省   山西省    广东省  广西壮族自治区  新疆维吾尔自治区    江苏省    江西省    河北省  \
date                                                                       
2020-01-27     75.0  13.0  151.0     46.0       5.0   47.0   48.0   18.0   
2020-01-28     95.0  20.0  208.0     51.0      10.0   70.0   72.0   33.0   
2020-01-29    130.0  30.0  282.0     58.0      15.0   99.0  109.0   48.0   
2020-01-30    158.0  35.0  354.0     78.0      14.0  129.0  162.0   65.0   
2020-01-31    184.0  39.0  436.0     87.0      19.0  168.0  240.0   82.0   
2020-02-01    206.0  47.0  535.0    100.0      18.0  202.0  286.0   96.0   
2020-02-02    230.0  56.0  632.0    111.0      21.0  236.0  333.0  104.0   
2020-02-03    259.0  66.0  725.0    127.0      24.0  271.0  391.0  113.0   
2020-02-04    275.0  74.0  813.0    139.0      29.0  308.0  476.0  126.0   
2020-02-05    307.0  81.0  895.0    150.0      32.0  341.0  548.0  135.0   

provinceName    河南省    浙江省   海南省      湖北省    湖南省   甘肃省    福建省   贵州省   辽宁省  \
date                                                                        
2020-01-27    133.0  128.0  33.0   1423.0  100.0  14.0   59.0   7.0  25.0   
2020-01-28    188.0  173.0  40.0   2714.0  143.0  22.0   80.0   9.0  32.0   
2020-01-29    206.0  296.0  43.0   3554.0  221.0  24.0   82.0   9.0  35.0   
2020-01-30    278.0  428.0  46.0   4586.0  277.0  26.0  101.0  12.0  41.0   
2020-01-31    354.0  537.0  64.0   5806.0  332.0  34.0  120.0  29.0  43.0   
2020-02-01    462.0  599.0  77.0   7240.0  389.0  46.0  144.0  29.0  64.0   
2020-02-02    493.0  661.0  64.0   9074.0  463.0  40.0  159.0  38.0  71.0   
2020-02-03    781.0  724.0  72.0  11177.0  521.0  51.0  179.0  46.0  74.0   
2020-02-04    675.0  829.0  80.0  13522.0  593.0  57.0  194.0  58.0  81.0   
2020-02-05    764.0  895.0  91.0  16678.0  661.0  57.0  205.0  64.0  89.0   

provinceName    重庆市    陕西省   青海省   黑龙江省  
date                                     
2020-01-27    110.0   35.0   6.0   21.0  
2020-01-28    132.0   46.0   NaN   30.0  
2020-01-29    147.0   56.0   NaN   38.0  
2020-01-30    182.0   63.0   6.0   44.0  
2020-01-31    266.0   87.0   8.0   59.0  
2020-02-01    247.0  101.0  18.0   80.0  
2020-02-02    275.0  116.0   9.0   95.0  
2020-02-03    312.0  128.0  14.0  121.0  
2020-02-04    344.0  142.0  15.0  155.0  
2020-02-05    376.0  165.0  17.0  190.0

In [499]:
dayUnique_gr_2 = dayUnique_gr.copy()

In [500]:
for i in range(len(dayUnique_gr)):
    for j in range(len(dayUnique_gr.columns)):
        if i == 0:
            pass
        else:
            now = dayUnique_gr.iloc[i,j]
            past = dayUnique_gr.iloc[i-1,j]
            dayUnique_gr_2.iloc[i,j] = (now-past)/past

In [501]:
dayUnique_gr_2.drop("2020-01-27",inplace=True)
dayUnique_gr_2.head()

provinceName       上海市       云南省    内蒙古自治区       北京市       吉林省       四川省  \
date                                                                       
2020-01-28    0.811321  0.692308  0.363636  0.137500  0.333333  0.304348   
2020-01-29    0.000000  0.250000 -0.466667  0.219780  0.125000  0.200000   
2020-01-30    0.166667  0.272727  0.125000 -0.189189  0.555556  0.314815   
2020-01-31    1.080357  0.185714  0.055556  1.888889  0.000000  0.246479   
2020-02-01   -0.274678  0.120482  0.210526 -0.353846  0.285714  0.169492   

provinceName       天津市   宁夏回族自治区       安徽省       山东省       山西省       广东省  \
date                                                                       
2020-01-28    0.090909  0.571429  0.514286  0.266667  0.538462  0.377483   
2020-01-29    0.291667  0.090909  0.462264  0.368421  0.500000  0.355769   
2020-01-30    0.032258  0.500000  0.290323  0.215385  0.166667  0.255319   
2020-01-31    0.031250  0.166667  0.185000  0.164557  0.114286  0.231638   
2020-02-01    0.242424  0.238095  0.253165  0.119565  0.205128  0.227064   

provinceName   广西壮族自治区  新疆维吾尔自治区       江苏省       江西省       河北省       河南省  \
date                                                                       
2020-01-28    0.108696  1.000000  0.489362  0.500000  0.833333  0.413534   
2020-01-29    0.137255  0.500000  0.414286  0.513889  0.454545  0.095745   
2020-01-30    0.344828 -0.066667  0.303030  0.486239  0.354167  0.349515   
2020-01-31    0.115385  0.357143  0.302326  0.481481  0.261538  0.273381   
2020-02-01    0.149425 -0.052632  0.202381  0.191667  0.170732  0.305085   

provinceName       浙江省       海南省       湖北省       湖南省       甘肃省       福建省  \
date                                                                       
2020-01-28    0.351562  0.212121  0.907238  0.430000  0.571429  0.355932   
2020-01-29    0.710983  0.075000  0.309506  0.545455  0.090909  0.025000   
2020-01-30    0.445946  0.069767  0.290377  0.253394  0.083333  0.231707   
2020-01-31    0.254673  0.391304  0.266027  0.198556  0.307692  0.188119   
2020-02-01    0.115456  0.203125  0.246986  0.171687  0.352941  0.200000   

provinceName       贵州省       辽宁省       重庆市       陕西省       青海省      黑龙江省  
date                                                                      
2020-01-28    0.285714  0.280000  0.200000  0.314286       NaN  0.428571  
2020-01-29    0.000000  0.093750  0.113636  0.217391       NaN  0.266667  
2020-01-30    0.333333  0.171429  0.238095  0.125000       NaN  0.157895  
2020-01-31    1.416667  0.048780  0.461538  0.380952  0.333333  0.340909  
2020-02-01    0.000000  0.488372 -0.071429  0.160920  1.250000  0.355932

In [502]:
dayUnique_gr_2 = dayUnique_gr_2.reset_index()

In [503]:
listofcolumns = []
for i in dayUnique_gr_2.columns:
    if i != "date":
        listofcolumns.append(i)

dayUnique_gr_2_melt = pd.melt(dayUnique_gr_2, id_vars=['date'],
                                value_vars= listofcolumns, 
                                var_name='ProvinceName')

In [504]:
dayUnique_gr_2_melt.head()

date ProvinceName     value
0  2020-01-28          上海市  0.811321
1  2020-01-29          上海市  0.000000
2  2020-01-30          上海市  0.166667
3  2020-01-31          上海市  1.080357
4  2020-02-01          上海市 -0.274678

In [505]:
px.line(dayUnique_gr_2_melt, x="date", y="value",color ='ProvinceName',
        title='Growth rate of coronavirus in each province')

In [506]:
px.bar(dayUnique_gr_2_melt,x="value", y="ProvinceName", color='ProvinceName', 
       orientation='h', height=800,title='Growth rate of coronavirus in each province',
       animation_frame="date",range_x = [0,2])